In [5]:
import conf

from strategies.bbrsi_strategy import BbRsiStrategy
from optimise_common import *

import datetime  # For datetime objects
from datetime import date
import backtrader as bt
import backtrader.analyzers as btanalyzers
import yfinance as yf

optimise = False
initial_cash = 20000
#initial_cash = 100000

# strategy-controls
printlog=False
print_trade_actions=True
lower_rsi=44 # 44 offered the higher 5-yr profit (150k from 30k initial investment)
loss_pct_threshold = 100 # Effectively full loss tolerance. using values such as 10-11% made little difference
inflection_profit_percentage_target = 5 # 5 showed best outcome for 5 year backtest
fixed_investment_amount=2500
# backtest window 
num_years = 5
year_offset = 0

# stock to test
tickers = high_performance_stock

warmup_date, start_date, end_date = optimisation_date_offsets(num_years, year_offset)
warmup_date, start_date, end_date = optimisation_dates(date(2024,9,6), datetime.datetime.today())

def pnl_report(strategy):
    total_pnl = 0
    # Unwind any open opositions
    for ticker in strategy.stock_pnl.keys():
        if strategy.getpositionbyname(ticker):
            position = strategy.getpositionbyname(ticker)
            data = strategy.getdatabyname(ticker)
            open_pnl = ((position.size * data.close[0])-(position.size*position.price))
            #print(f'{ticker} open PNL: {position.size:2f} x {data.close[0]:2f} - {position.size:2f} x {position.price:2f} = {open_pnl:2f}')
            strategy.stock_pnl[ticker] += open_pnl
    for ticker in strategy.stock_pnl.keys():
        print(f'{ticker} PNL: {strategy.stock_pnl[ticker]:.2f}')
        total_pnl += strategy.stock_pnl[ticker]
    print(f'Total PNL: {total_pnl:.2f}')

def strategy_completed_callback(strategy):
    final_value = strategy.broker.get_value()
    print("strategy_completed_callback stats: " + 
        f'lower_rsi: {strategy.params.lower_rsi}, ' +
        f'fixed_investment_amount: {strategy.params.fixed_investment_amount}, ' +
        f'inflection_profit_percentage_target: {strategy.params.inflection_profit_percentage_target}, ' +
        f'bb_low_crossover_loss_tolerance: {strategy.params.bb_low_crossover_loss_tolerance}, ' +
        
        f'final_portolio_value: {final_value:.0f}'
    )
    stats.append({'lower_rsi': strategy.params.lower_rsi, 
        'fixed_investment_amount': strategy.params.fixed_investment_amount,
        'inflection_profit_percentage_target': strategy.params.inflection_profit_percentage_target,
        'bb_low_crossover_loss_tolerance': strategy.params.bb_low_crossover_loss_tolerance,
        'final_portolio_value': round(strategy.broker.getvalue())}) 

stats = []

if __name__ == '__main__':
    # Create a cerebro entity
    cerebro = create_cerebro()

    if not optimise:
        # Add a strategy (see strategy-controls)
        cerebro.addstrategy(BbRsiStrategy,
                            start_date = start_date,
                            printlog = printlog,
                            print_trade_actions = print_trade_actions,
                            lower_rsi = lower_rsi,
                            loss_pct_threshold = loss_pct_threshold,
                            fixed_investment_amount = fixed_investment_amount,
                            inflection_profit_percentage_target = inflection_profit_percentage_target,
                            custom_callback=pnl_report)
    else:
        strats = cerebro.optstrategy(
            BbRsiStrategy,
            start_date = start_date,
            lower_rsi = 44, # range(42, 45, 1), #, 44 (5-year best)
            inflection_profit_percentage_target = 5, #[2,3,4,5,6,7], # 5 (5-year best)
            bb_low_crossover_loss_tolerance = range(0,11),
            fixed_investment_amount = range(3000, 6000, 500), # 4000 (5-year best)
            custom_callback=strategy_completed_callback,
            )
        cerebro.addanalyzer(btanalyzers.DrawDown, _name='drawdown')

    add_data_feed(cerebro, tickers, warmup_date, start_date, end_date)
    set_cash(cerebro, initial_cash)
    
    execute_cerebro(cerebro, optimise, stats)

    
%matplotlib inline
import matplotlib.pyplot as plt
from pylab import rcParams #Creates parameters for our plot
if not optimise:
    print(f'Plotting graphs ...')
    # Plot the result
    rcParams['figure.figsize'] = 16, 6 * len(tickers) #size
    rcParams['figure.facecolor'] = '#eeeeee' #Color scheme
    plt.plot() #The Plot Code
    plt.close()
    cerebro.plot(iplot=True, volume=False)
 

tickers: ['AAPL', 'ABBV', 'ADBE', 'AMD', 'AMZN', 'AVGO', 'BAC', 'BRK-B', 'COST', 'CRM', 'CVX', 'GOOG', 'HD', 'JNJ', 'JPM', 'KO', 'LLY', 'MA', 'META', 'MRK', 'MSFT', 'NFLX', 'NVDA', 'ORCL', 'PEP', 'PFE', 'PG', 'TMO', 'TSLA', 'UNH', 'V', 'WMT', 'XOM']
time window = warmup-date: 2024-05-09, start-date: 2024-09-06, end-data: 2024-09-27 22:57:11.255588


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

2024-09-09 BUY CVX because CVX Close (138.56,140.30) above Bollinger bottom (139.77) while RSI (35.60) below 44.00
2024-09-09 BUY MSFT because MSFT Close (401.70,405.72) above Bollinger bottom (401.98) while RSI (40.50) below 44.00
2024-09-11 BUY GOOG because GOOG Close (150.01,152.15) above Bollinger bottom (149.24) while RSI (32.49) below 44.00
2024-09-11 BUY JPM because JPM Close (205.56,207.23) above Bollinger bottom (206.42) while RSI (41.70) below 44.00
2024-09-12 BUY XOM because XOM Close (109.72,111.23) above Bollinger bottom (109.83) while RSI (40.56) below 44.00
2024-09-17 BUY AAPL because AAPL Close (216.32,216.79) above Bollinger bottom (216.27) while RSI (40.11) below 44.00
2024-09-19 BUY ADBE because ADBE Close (508.13,526.44) above Bollinger bottom (512.66) while RSI (41.04) below 44.00
2024-09-23 BUY PEP because PEP Close (171.18,172.11) above Bollinger bottom (171.24) while RSI (41.38) below 44.00
2024-09-25 BUY PEP because PEP Close (169.92,169.40) above Bollinger bot

<IPython.core.display.Javascript object>

/home/joao/code/trade-advisor/.venv/lib/python3.10/site-packages/backtrader/plot/locator.py:184: UserWarning: AutoDateLocator was unable to pick an appropriate interval for this date range. It may be necessary to add an interval value to the AutoDateLocator's intervald dictionary. Defaulting to 14.
  warnings.warn('AutoDateLocator was unable to pick an '
